## **Import**

In [1]:
import os, glob
import numpy as np
import matplotlib.pyplot as plt
from astropy.io import fits

from ciao_contrib.runtool import chandra_repro, deflare, dmcopy, dmimgcalc, dmfilth, dmkeypar, dmextract, wavdetect
from ciao_contrib.cda.data import download_chandra_obsids
import ciao_contrib.logger_wrapper as lw

path = os.getcwd()

## **Download OBSID**

To find OBSIDs for a specific object, use [ChaSeR](https://cda.harvard.edu/chaser/) or `find_chandra_obsid()`

In [3]:
galaxy = "NGC4778"
OBSIDs = [10462, 10874]
chips = "6,7"

os.mkdir(f"{path}/{galaxy}")
os.chdir(f"{path}/{galaxy}")

for OBSID in OBSIDs:
    if not os.path.exists(f"{OBSID}"):
        lw.initialize_logger("download", verbose=1)
        download_chandra_obsids([OBSID])
    else:
        print(f"OBSID {OBSID} already downloaded")


  Type     Format      Size  0........H.........1  Download Time Average Rate
  ---------------------------------------------------------------------------
  evt1     fits      205 Mb  ####################       1 m 27 s  2396.2 kb/s
  vvref    pdf       131 Mb  ####################           51 s  2607.8 kb/s
  evt2     fits       33 Mb  ####################           16 s  2114.9 kb/s
  asol     fits       15 Mb  ####################            7 s  2076.8 kb/s
  mtl      fits        3 Mb  ####################            2 s  1316.9 kb/s
  stat     fits        2 Mb  ####################            2 s  823.6 kb/s
  aqual    fits        1 Mb  ####################            1 s  942.1 kb/s
  cntr_img jpg       560 Kb  ####################          < 1 s  579.9 kb/s
  bias     fits      493 Kb  ####################          < 1 s  506.3 kb/s
  bias     fits      448 Kb  ####################          < 1 s  478.6 kb/s
  bias     fits      444 Kb  ####################          < 1 s  46

## **Chandra repro**

In [6]:
os.getcwd()

'/home/plsek/Github/Tutorials/CIAO/NGC4778'

In [7]:
for OBSID in OBSIDs:
    evt = glob.glob(f"{OBSID}/secondary/*evt1.fits*")[0]
    vfaint = "yes" if dmkeypar(evt, "DATAMODE", echo=True) == "VFAINT" else "no"

    if not os.path.exists(f"{OBSID}_repro"):
        os.system(f"chandra_repro {OBSID} {OBSID}_repro check_vf_pha={vfaint} clob+")
    else:
        print(f"OBSID {OBSID} already reprocessed")


Running chandra_repro
version: 22 January 2023


Processing input directory '/home/plsek/Github/Tutorials/CIAO/NGC4778/10462'

No boresight correction update to asol file is needed.
Resetting afterglow status bits in evt1.fits file...

Running acis_build_badpix and acis_find_afterglow to create a new bad pixel file...

Running acis_process_events to reprocess the evt1.fits file...
Output from acis_process_events:
# acis_process_events (CIAO 4.16.0): The following error occurred 11 times:
	dsAPEPULSEHEIGHTERR -- WARNING: pulse height is less than split threshold when performing serial CTI adjustment.
Filtering the evt1.fits file by grade and status and time...
Applying the good time intervals from the flt1.fits file...
The new evt2.fits file is: /home/plsek/Github/Tutorials/CIAO/NGC4778/10462_repro/acisf10462_repro_evt2.fits

Updating the event file header with chandra_repro HISTORY record
Creating FOV file...
Setting observation-specific bad pixel file in local ardlib.par.

Cleaning u

## **Reproject & flux_obs**

In [8]:
evts = ""
for OBSID in OBSIDs:
    evt = glob.glob(f"{OBSID}_repro/*evt2.fits")[0]
    evts += f"{evt}[ccd_id={chips}],"

os.system(f'reproject_obs infiles="{evts}" outroot=reproj/ clob+')

for OBSID in OBSIDs:
    os.system(f"cp reproj/{OBSID}* {OBSID}_repro/")

Running reproject_obs
Version: 20 October 2023

Verifying 2 observations.
Calculating new tangent point.
New tangent point: RA=12h 53m 7.962s Dec=-9d 11' 29.27"

Observations to be reprojected:

  Obsid  Obs Date   Exp    DETNAM     SIM_Z    FP   Sepn   PA  
                   (ks)                (mm)    (K)   (')  (deg)
---------------------------------------------------------------
1 10462 2009-03-02  67.1 ACIS-23567  -190.140 153.6  < 3"    +8
2 10874 2009-03-03  51.4 ACIS-23567  -190.140 153.6  < 3"  -172

Running tasks in parallel with 16 processors.
Reprojecting 2 event files to a common tangent point.
Merging reprojected events files to reproj/merged_evt.fits

The following files were created:

The reprojected FOV files:
     reproj/10462.fov
     reproj/10874.fov

The combined FOV file:
     reproj/merged.fov

The reprojected event files:
     reproj/10462_reproj_evt.fits
     reproj/10874_reproj_evt.fits

The merged event file:
     reproj/merged_evt.fits



In [9]:
evts = ""
for OBSID in OBSIDs:
    evt = glob.glob(f"{OBSID}_repro/*reproj_evt.fits")[0]
    evts += f"{evt} "

os.system(f'flux_obs infiles="{evts}" outroot=merged/ bin=1 psfecf=0.9 clob+')

Running flux_obs
Version: 05 November 2021

Verifying 2 observations.
Using CSC ACIS broad science energy band.
Calculating the output grid

The merged images will have 1908 by 2346 pixels, a pixel size of 0.492 arcsec,
    and cover x=3052.5:4960.5:1, y=3136.5:5482.5:1.

Creating the fluxed images for 2 observations in parallel.
Creating 2 aspect histograms for obsid 10462
Creating 2 aspect histograms for obsid 10874
Creating 2 instrument maps for obsid 10874
Creating 2 instrument maps for obsid 10462
Creating 2 exposure maps for obsid 10874
Creating 2 exposure maps for obsid 10462
Combining 2 exposure maps for obsid 10874
Combining 2 exposure maps for obsid 10462
Thresholding data for obsid 10874
Thresholding data for obsid 10462
Exposure-correcting image for obsid 10874
Exposure-correcting image for obsid 10462
Creating PSF map for obsid 10874
Creating PSF map for obsid 10462

Combining 2 observations.

The following files were created:

The co-added clipped counts image is:
     me

0

## **Wavdetect**

In [ ]:
os.chdir(f"{path}/{galaxy}/merged")

# Maybe will end with an error
wavdetect("broad_thresh.img", outfile="wav.reg", clobber=True,
          psffile="broad_thresh.psfmap", expfile="broad_thresh.expmap",
          scellfile="wav.scell", imagefile="wav.img", defnbkgfile="wav.bkg",
          scales="2,4,8", maxiter=5, sigthresh=1e-5, ellsigma=3.5)

os.chdir("..")

Open the resulting region file in DS9:

```bash
$ ds9 broad_thresh.img -region wav.reg
```

Check detected sources by eye and look for overlaping point sources - if present, remove one the of the sources and make the other one bigger, so that it covers the area of both sources. Usually, it's better to also remove the central AGN from the list of point sources. Then save the resulting region file as **`sources.reg`** in the **CIAO** format and using **FK5 (WCS)** coordinates and save it into the main repository (in this case NGC4778).

<img src="figures/before.png" align=left width=600>
<img src="figures/rightarrow.png" style="position:absolute;left:47%;top:50%;width:100px;margin:auto;text-align:center;">
<img src="figures/after.png" align=right width=600>

In [15]:
!ds9 merged/broad_thresh.img -region merged/wav.reg

pget: /home/plsek/anaconda3/envs/ciao/binexe/../lib/././libtinfo.so.6: no version information available (required by /home/plsek/anaconda3/envs/ciao/binexe/../lib/./libreadline.so.8)


## **Extract lightcurve & deflare**

In [14]:
for OBSID in OBSIDs:
    os.chdir(f"{OBSID}_repro")

    evt = glob.glob("*_reproj_evt.fits")[0]

    dmextract(f"{evt}[exclude sky=region(../sources.reg)][bin time=::137.12, energy=500:7000]",\
            f"{OBSID}.lc", opt="ltc1", clobber=True)
    
    # DEFLARE LIGHT CURVE
    deflare.punlearn()
    # deflare.mean = 12.5
    deflare.method = "clean"
    deflare.stddev = 4
    print(deflare(f"{OBSID}.lc", f"{OBSID}.gti", save=f"{OBSID}_deflared"))

    dmcopy(f"{evt}[@{OBSID}.gti]", f"{OBSID}_clean.fits", clobber=True)

    os.chdir("..")

Parameters used to clean the lightcurve are:
  script version = 16 May 2023
  mean           = None
  clip           = 3
  sigma          = 4
  minfrac        = 0.1
  outfile        = 10462.gti
  plot           = True
  rateaxis       = y
  color          = lime
  pattern        = solid
  pattern color  = red

Total number of bins in lightcurve   = 510
Max length of one bin                = 135.328 s
Num. bins with a smaller exp. time   = 2
Num. bins with exp. time = 0         = 13
Number of bins with a rate of 0 ct/s = 13

Calculated an initial mean (sigma-clipped) rate of 4.84379 ct/s
Lightcurve limits clipped using 4 sigma's about this mean
Filtering lightcurve between rates of 4.08703 and 5.60055 ct/s
Number of good time bins = 497
Rate filter:  4.08703231792315 <= count_rate < 5.600552560371751
Mean level of filtered lightcurve = 4.846304975884615 ct/s

GTI limits calculated using a count-rate filter:
  (count_rate>4.08703231792315 && count_rate<5.600552560371751)

The correspondi

## **Flux_obs**

In [15]:
evts = ""
for OBSID in OBSIDs:
    evt = glob.glob(f"{OBSID}_repro/*clean.fits*")[0]
    evts += f"{evt} "

os.system(f'flux_obs infiles="{evts}" outroot=flux/ bin=1 psfecf=0.9 clob+')
os.system(f'flux_obs infiles="{evts}" outroot=flux_rgb/ bin=1 band="csc" clob+') # FOR FALSE RGB IMAGE

Running flux_obs
Version: 05 November 2021

Verifying 2 observations.
Using CSC ACIS broad science energy band.
Calculating the output grid

The merged images will have 1908 by 2346 pixels, a pixel size of 0.492 arcsec,
    and cover x=3052.5:4960.5:1, y=3136.5:5482.5:1.

Creating the fluxed images for 2 observations in parallel.
Creating 2 aspect histograms for obsid 10462
Creating 2 aspect histograms for obsid 10874
Creating 2 instrument maps for obsid 10874
Creating 2 instrument maps for obsid 10462
Creating 2 exposure maps for obsid 10874
Creating 2 exposure maps for obsid 10462
Combining 2 exposure maps for obsid 10874
Thresholding data for obsid 10874
Exposure-correcting image for obsid 10874
Creating PSF map for obsid 10874
Combining 2 exposure maps for obsid 10462
Thresholding data for obsid 10462
Exposure-correcting image for obsid 10462
Creating PSF map for obsid 10462

Combining 2 observations.

The following files were created:

The co-added clipped counts image is:
     fl

0

In [16]:
os.system("cp flux/broad_flux.img broad.fits")
os.system("cp flux_rgb/soft_flux.img soft.fits")
os.system("cp flux_rgb/medium_flux.img medium.fits")
os.system("cp flux_rgb/hard_flux.img hard.fits")

# CREATE FALSE RGB IMAGE
os.system(f"ds9 -rgb -red soft.fits -green medium.fits -blue hard.fits -rgb lock scale yes \
          -rgb lock colorbar yes -rgb lock smooth yes -log -smooth -export {galaxy}_Chandra_RGB.png")

0

## **Fill sources**

In [29]:
def create_fill_backgrounds(a=1.1, b=1.5):
    # load data from sources.reg
    RA, DEC, R1, R2, DIR, mag = [], [], [], [], [], []
    with open(f"sources.reg", "r") as file:
        for line in file.readlines():
            vals = line.split(",")
            RA.append(vals[0].split("(")[1])
            DEC.append(vals[1])
            if vals[0][0] == "c":
                R1.append(float(vals[2][:-3]))
                R2.append(float(vals[2][:-3]))
                DIR.append("0.00)\n")
                mag.append(vals[2][-3])
            else:
                R1.append(float(vals[2][:-1]))
                R2.append(float(vals[3][:-1]))
                DIR.append(vals[4])
                mag.append(vals[2][-1])

    # Create directory for temporary files
    if not os.path.exists(".tmp"):
        os.mkdir(".tmp")

    # make new sources.reg with slightly higher radius and save it to cavities folder
    with open(f".tmp/sources_new.reg", "w") as file:
        for i in range(len(RA)):
            ellipses = "ellipse({0},{1},{2:.3g}{5},{3:.3g}{5},{4}".format(RA[i], DEC[i] ,R1[i] * a, R2[i] * a, DIR[i], mag[i])
            file.write(ellipses)

    # make background region file with elliptical anuli with radii between a and b times previous ellipse
    with open(f".tmp/sources_bkg.reg", "w") as file:
        for i in range(len(RA)):
            src = "ellipse({0},{1},{2:.3g}{5},{3:.3g}{5},{4}".format(RA[i], DEC[i], R1[i] * b, R2[i] * b, DIR[i][:-1], mag[i])
            bkg = "*!ellipse({0},{1},{2:.3g}{5},{3:.3g}{5},{4}".format(RA[i], DEC[i], R1[i] * a, R2[i] * a, DIR[i] ,mag[i])
            file.write(src + bkg)
            #file.write("ellipse{0},{1},{2}',{3}',{4}',{5}',{6}".format(RA[i][7:],DEC[i],R1[i]*1.1,R2[i]*1.1,R1[i]*1.5,R2[i]*1.5,DIR[i]))

def fill_sources(fname):
    DIR = "flux" if "broad" in fname else "flux_rgb"
    # FILL POINT SOURCES
    dmfilth(f"{DIR}/{fname}_thresh.img[exclude sky=region(.tmp/sources_new.reg)]", f".tmp/{fname}_filled.fits", method="POISSON",\
            srclist="@.tmp/sources_new.reg", bkglist="@.tmp/sources_bkg.reg", clobber=True)
    
    dmimgcalc(f".tmp/{fname}_filled.fits,merged/broad_thresh.expmap", infile2=None, outfile=f"{fname}_filled.fits", op=f"imgout=img1/(img2+1)", clobber=True)

In [30]:
# CREATE BACKGROUND REGION AROUND EACH POINT SOURCE
create_fill_backgrounds(a=1.1, b=1.6)

In [31]:
fill_sources("broad")

fill_sources("soft")

fill_sources("medium")

fill_sources("hard")

In [32]:
os.system(f"ds9 -rgb -red soft_filled.fits -green medium_filled.fits -blue hard_filled.fits \
          -rgb lock scale yes -rgb lock colorbar yes -rgb lock smooth yes -log -smooth -export {galaxy}_Chandra_filled_RGB.png")

0